# 강의 11주차: midm-food-order-understanding

1. KT-AI/midm-bitext-S-7B-inst-v1 를 주문 문장 이해에 미세 튜닝

- food-order-understanding-small-3200.json (학습)
- food-order-understanding-small-800.json (검증)


종속적인 필요 내용
- huggingface 계정 설정 및 llama-2 사용 승인
- 로깅을 위한 wandb (log 기록됨)

In [ ]:
pip install transformers peft accelerate optimum bitsandbytes trl wandb einops

In [ ]:
import os
from dataclasses import dataclass, field
from typing import Optional
import re

import torch
import tyro
from accelerate import Accelerator
from datasets import load_dataset, Dataset
from peft import AutoPeftModelForCausalLM, LoraConfig
from tqdm import tqdm
from transformers import (
    AutoModelForCausalLM,
    AutoTokenizer,
    BitsAndBytesConfig,
    TrainingArguments,
)

from trl import SFTTrainer

from trl.trainer import ConstantLengthDataset

/usr/local/lib/python3.10/dist-packages/trl/trainer/ppo_config.py:141: UserWarning: The `optimize_cuda_cache` arguement will be deprecated soon, please use `optimize_device_cache` instead.
  warnings.warn(


In [ ]:
from huggingface_hub import notebook_login

notebook_login()

드라이브 마운트 후 파일 업로드
- food-order-understanding-small-3200.json
- food-order-understanding-small-800.json

In [ ]:
from google.colab import drive
drive.mount('/gdrive')

Drive already mounted at /gdrive; to attempt to forcibly remount, call drive.mount("/gdrive", force_remount=True).


In [ ]:
# /gdrive/MyDrive/food-order-understanding-small-3200.json
# /gdrive/MyDrive/food-order-understanding-small-800.json

# 매개 변수 설정

In [ ]:
@dataclass
class ScriptArguments:
    cache_dir: Optional[str] = field(
        default=None, metadata={"help": "the cache dir"}
    )
    model_name: Optional[str] = field(
        default="KT-AI/midm-bitext-S-7B-inst-v1", metadata={"help": "the model name"}
    )

    dataset_name: Optional[str] = field(
        default="nsmc",
        metadata={"help": "the dataset name"},
    )
    seq_length: Optional[int] = field(
        default=128, metadata={"help": "the sequence length"}
    )
    num_workers: Optional[int] = field(
        default=8, metadata={"help": "the number of workers"}
    )
    training_args: TrainingArguments = field(
        default_factory=lambda: TrainingArguments(
            output_dir="./results",
            max_steps=500,
            logging_steps=20,
            #save_steps=10,
            per_device_train_batch_size=1, #1로 할 수 밖에 없음, 모델 커서 메모리 부족해서
            per_device_eval_batch_size=1,
            gradient_accumulation_steps=2, #얘는 큰 지장 ㄴ
            gradient_checkpointing=False,#트루로두면 error나는 모델있음, 트루면 메모리 이득임
            group_by_length=False,
            learning_rate=1e-4,
            lr_scheduler_type="cosine",
            # warmup_steps=100,
            warmup_ratio=0.03,
            max_grad_norm=0.3,
            weight_decay=0.05,
            save_total_limit=20,
            save_strategy="epoch",
            num_train_epochs=1,
            optim="paged_adamw_32bit",
            fp16=False,
            remove_unused_columns=False,
            report_to="wandb",
        )
    )

    packing: Optional[bool] = field(
        default=True, metadata={"help": "whether to use packing for SFTTrainer"}
    )

    peft_config: LoraConfig = field(
        default_factory=lambda: LoraConfig(
            r=8, #랭크
            lora_alpha=16,
            lora_dropout=0.05,
            target_modules=["c_attn", "c_proj", "c_fc"],
            bias="none",
            task_type="CAUSAL_LM",
        )
    )

    merge_with_final_checkpoint: Optional[bool] = field(
        default=False, metadata={"help": "Do only merge with final checkpoint"}
    )

# 유틸리티

In [ ]:
def chars_token_ratio(dataset, tokenizer, nb_examples=400):
    """
    Estimate the average number of characters per token in the dataset.
    """
    total_characters, total_tokens = 0, 0
    for _, example in tqdm(zip(range(nb_examples), iter(dataset)), total=nb_examples):
        text = prepare_sample_text(example)
        total_characters += len(text)
        if tokenizer.is_fast:
            total_tokens += len(tokenizer(text).tokens())
        else:
            total_tokens += len(tokenizer.tokenize(text))

    return total_characters / total_tokens


def print_trainable_parameters(model):
    """
    Prints the number of trainable parameters in the model.
    """
    trainable_params = 0
    all_param = 0
    for _, param in model.named_parameters():
        all_param += param.numel()
        if param.requires_grad:
            trainable_params += param.numel()
    print(
        f"trainable params: {trainable_params} || all params: {all_param} || trainable%: {100 * trainable_params / all_param}"
    )

# 데이터 로딩

In [ ]:
def prepare_sample_text(example): #헬퍼함수
    """Prepare the text from a sample of the dataset."""

    prompt_template = """###System;{System}
    ###User;{User}
    ###Midm;"""

    default_system_msg = (
        "너는 사용자가 작성한 리뷰를 긍정, 부정 중 하나로 판단해야 한다."
    )

    text = (
        prompt_template.format(System=default_system_msg, User=example["input"],Midm=example["output"])
    )

    return text

In [ ]:
def create_datasets(tokenizer, args):
    train_data = Dataset.from_json(args.dataset_name)

    train_data = train_data.select(range(2000))

    chars_per_token = chars_token_ratio(train_data, tokenizer)
    print(f"The character to token ratio of the dataset is: {chars_per_token:.2f}")

    train_dataset = ConstantLengthDataset(
        tokenizer,
        train_data,
        formatting_func=prepare_sample_text,
        infinite=True,
        seq_length=args.seq_length,
        chars_per_token=chars_per_token,
    )
    return train_dataset #청크단위로 끊어서 미니배치 만들어줌

# 미세 튜닝용 모델 로딩

In [ ]:
script_args = ScriptArguments(
    num_workers=2,
    seq_length=64, # = 청크사이즈, 좋은 성능이려면 청크사이즈가 커야되지만 메모리가 부족할수도
    dataset_name='/gdrive/MyDrive/food-order-understanding-small-3200.json',
    # model_name='KT-AI/midm-bitext-S-7B-inst-v1',
    model_name='jangmin/midm-7b-safetensors-only',

    )

In [ ]:
script_args.training_args.logging_steps = 50 # 그래디언트 업데이트 50번만 진행
script_args.training_args.max_steps = 300
script_args.training_args.output_dir = '/gdrive/MyDrive/lora-midm-7b-food-order-understanding' #학습수행된 결과물은 여기에 저장
script_args.training_args.run_name = 'midm-7b-food-order-understanding' #실행식별자 => 로깅정보가 여기에 담김

In [ ]:
print(script_args)

ScriptArguments(cache_dir=None, model_name='jangmin/midm-7b-safetensors-only', dataset_name='/gdrive/MyDrive/food-order-understanding-small-3200.json', seq_length=64, num_workers=2, training_args=TrainingArguments(
_n_gpu=1,
adafactor=False,
adam_beta1=0.9,
adam_beta2=0.999,
adam_epsilon=1e-08,
auto_find_batch_size=False,
bf16=False,
bf16_full_eval=False,
data_seed=None,
dataloader_drop_last=False,
dataloader_num_workers=0,
dataloader_pin_memory=True,
ddp_backend=None,
ddp_broadcast_buffers=None,
ddp_bucket_cap_mb=None,
ddp_find_unused_parameters=None,
ddp_timeout=1800,
debug=[],
deepspeed=None,
disable_tqdm=False,
dispatch_batches=None,
do_eval=False,
do_predict=False,
do_train=False,
eval_accumulation_steps=None,
eval_delay=0,
eval_steps=None,
evaluation_strategy=no,
fp16=False,
fp16_backend=auto,
fp16_full_eval=False,
fp16_opt_level=O1,
fsdp=[],
fsdp_config={'min_num_params': 0, 'xla': False, 'xla_fsdp_grad_ckpt': False},
fsdp_min_num_params=0,
fsdp_transformer_layer_cls_to_wrap=Non

In [ ]:
bnb_config = BitsAndBytesConfig(
    load_in_4bit=True,
    bnb_4bit_quant_type="nf4",
    bnb_4bit_compute_dtype=torch.bfloat16,
) #원본모델 4비트로 양자화

원본인 'KT-AI/midm-bitext-S-7B-inst-v1' 는 *.bin 형태로 모델을 제공한다.
- 코랩에서 CPU 메모리 부족 발생

해결책
- safetensors로 변환한 모델을 업로드 하고 이를 사용하기로 한다.

In [ ]:
base_model = AutoModelForCausalLM.from_pretrained(
    script_args.model_name,
    quantization_config=bnb_config,
    device_map="auto",  # {"": Accelerator().local_process_index},
    trust_remote_code=True,
    use_auth_token=True,
    cache_dir=script_args.cache_dir,
)
base_model.config.use_cache = False #사용하면 캐시에 다운로드받은 게 있으면 그거 사용할 수 있음, 구글드라이브를 캐시 디렉토리로 사용하면 캐시역할을 못함=> 어차피 코랩이 빠르니까 그냥 로딩해서 쓰자

/usr/local/lib/python3.10/dist-packages/transformers/models/auto/auto_factory.py:472: FutureWarning: The `use_auth_token` argument is deprecated and will be removed in v5 of Transformers. Please use `token` instead.
  warnings.warn(


Loading checkpoint shards:   0%|          | 0/5 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/transformers/utils/hub.py:374: FutureWarning: The `use_auth_token` argument is deprecated and will be removed in v5 of Transformers. Please use `token` instead.
  warnings.warn(


In [ ]:
base_model
#linear모듈들이 다 4비트로 바껴있음, 아직 peft모델은 붙이지않음
#토큰의사이즈도 크고 컨택스트의 길이도 길어서 메모리를 현재 많이 차지하고있음

MidmLMHeadModel(
  (transformer): MidmModel(
    (wte): Embedding(72192, 4096)
    (rotary_pos_emb): RotaryEmbedding()
    (drop): Dropout(p=0.0, inplace=False)
    (h): ModuleList(
      (0-31): 32 x MidmBlock(
        (ln_1): LayerNorm((4096,), eps=1e-05, elementwise_affine=True)
        (attn): MidmAttention(
          (c_attn): Linear4bit(in_features=4096, out_features=12288, bias=False)
          (c_proj): Linear4bit(in_features=4096, out_features=4096, bias=False)
          (attn_dropout): Dropout(p=0.0, inplace=False)
          (resid_dropout): Dropout(p=0.0, inplace=False)
        )
        (ln_2): LayerNorm((4096,), eps=1e-05, elementwise_affine=True)
        (mlp): MidmMLP(
          (c_fc): Linear4bit(in_features=4096, out_features=21760, bias=False)
          (c_proj): Linear4bit(in_features=10880, out_features=4096, bias=False)
          (dropout): Dropout(p=0.0, inplace=False)
        )
      )
    )
    (ln_f): LayerNorm((4096,), eps=1e-05, elementwise_affine=True)
  )
 

In [ ]:
peft_config = script_args.peft_config

In [ ]:
peft_config

LoraConfig(peft_type=<PeftType.LORA: 'LORA'>, auto_mapping=None, base_model_name_or_path=None, revision=None, task_type='CAUSAL_LM', inference_mode=False, r=8, target_modules={'c_attn', 'c_proj', 'c_fc'}, lora_alpha=16, lora_dropout=0.05, fan_in_fan_out=False, bias='none', modules_to_save=None, init_lora_weights=True, layers_to_transform=None, layers_pattern=None, rank_pattern={}, alpha_pattern={}, megatron_config=None, megatron_core='megatron.core', loftq_config={})

In [ ]:
tokenizer = AutoTokenizer.from_pretrained(
    'KT-AI/midm-bitext-S-7B-inst-v1',
    # script_args.model_name,
    trust_remote_code=True,
    cache_dir=script_args.cache_dir,
)

#미묘한부분
if getattr(tokenizer, "pad_token", None) is None:
    tokenizer.pad_token = tokenizer.eos_token #패드토큰을 eos token으로 사용
tokenizer.padding_side = "right"  # Fix weird overflow issue with fp16 training

tokenizer.add_special_tokens(dict(bos_token='<s>'))

base_model.config.pad_token_id = tokenizer.pad_token_id
base_model.config.bos_token_id = tokenizer.bos_token_id

In [ ]:
training_args = script_args.training_args

In [ ]:
train_dataset = create_datasets(tokenizer, script_args)

100%|██████████| 400/400 [00:00<00:00, 2392.09it/s]

The character to token ratio of the dataset is: 1.48



/usr/local/lib/python3.10/dist-packages/trl/trainer/utils.py:548: UserWarning: The passed formatting_func has more than one argument. Usually that function should have a single argument `example` which corresponds to the dictionary returned by each element of the dataset. Make sure you know what you are doing.
  warnings.warn(


In [ ]:
len(train_dataset)

2000

In [ ]:
trainer = SFTTrainer(
    model=base_model,
    train_dataset=train_dataset,
    eval_dataset=None,
    peft_config=peft_config, #중요
    packing=script_args.packing,
    max_seq_length=script_args.seq_length, #청크사이즈 설정
    tokenizer=tokenizer,
    args=training_args,
)

/usr/local/lib/python3.10/dist-packages/trl/trainer/sft_trainer.py:267: UserWarning: You passed `packing=True` to the SFTTrainer, and you are training your model with `max_steps` strategy. The dataset will be iterated until the `max_steps` are reached.
  warnings.warn(


In [ ]:
base_model #내부에 peft_config 사용 => 로라 어댑터 붙여짐

MidmLMHeadModel(
  (transformer): MidmModel(
    (wte): Embedding(72192, 4096)
    (rotary_pos_emb): RotaryEmbedding()
    (drop): Dropout(p=0.0, inplace=False)
    (h): ModuleList(
      (0-31): 32 x MidmBlock(
        (ln_1): LayerNorm((4096,), eps=1e-05, elementwise_affine=True)
        (attn): MidmAttention(
          (c_attn): lora.Linear4bit(
            (base_layer): Linear4bit(in_features=4096, out_features=12288, bias=False)
            (lora_dropout): ModuleDict(
              (default): Dropout(p=0.05, inplace=False)
            )
            (lora_A): ModuleDict(
              (default): Linear(in_features=4096, out_features=8, bias=False)
            )
            (lora_B): ModuleDict(
              (default): Linear(in_features=8, out_features=12288, bias=False)
            )
            (lora_embedding_A): ParameterDict()
            (lora_embedding_B): ParameterDict()
          )
          (c_proj): lora.Linear4bit(
            (base_layer): Linear4bit(in_features=4096,

In [ ]:
base_model.device

device(type='cuda', index=0)

In [ ]:
print_trainable_parameters(base_model)

trainable params: 16744448 || all params: 3821510656 || trainable%: 0.4381630592527648


midm 모델을 주문 문장 이해에 적용시 특징
- 모델 로딩 과정에서 CPU도 5.1기가, 디스크 42.4기가, GPU 메모리: 7,4 기가

구글 코랩 T-4 GPU: 300스텝 (13:47초 예상)

시퀀스 길이 384의 경우
- 14.7 G / 15.0 G 사용
- 메모리 오버플로우 발생시 이보다 줄일 것

In [ ]:
trainer.train() # wandb 가입해야함

wandb: Currently logged in as: 20211397. Use `wandb login --relogin` to force relogin


TrainOutput(global_step=300, training_loss=1.1707455444335937, metrics={'train_runtime': 778.6233, 'train_samples_per_second': 0.771, 'train_steps_per_second': 0.385, 'total_flos': 1552584749875200.0, 'train_loss': 1.1707455444335937, 'epoch': 0.3})

In [ ]:
script_args.training_args.output_dir

'/gdrive/MyDrive/lora-midm-7b-food-order-understanding'

In [ ]:
trainer.save_model(script_args.training_args.output_dir)

# 추론 테스트

In [ ]:
from transformers import pipeline, TextStreamer

In [ ]:
instruction_prompt_template = """
###System;너는 사용자의 리뷰를 긍정,부정 중 하나로만 판단해야 한다.
### 리뷰 문장: 진짜 재밌다 ### 분류 결과: 긍정
###System;너는 사용자의 리뷰를 긍정,부정 중 하나로만 판단해야 한다.
### 리뷰 문장: 나 잘 뻔 했잖아 영화보고 지루해서 ### 분류 결과: 부정
###System;너는 사용자의 리뷰를 긍정,부정 중 하나로만 판단해야 한다.
### 리뷰 문장: 어떻게 이렇게까지 재미없을 수가 있지 ### 분류 결과: 부정
###System;너는 사용자의 리뷰를 긍정,부정 중 하나로만 판단해야 한다.
### 리뷰 문장: 열린결말 영화 좋아하는데 이 영화가 열린결말이야 ### 분류 결과: 긍정

"""
prompt_template = """###System;{System}
###User;{User}
###Midm;"""

default_system_msg = (
    "너는 사용자의 리뷰를 긍정,부정 중 하나로만 판단해야 한다."
)

In [ ]:
evaluation_queries = [
    "이게 재밌다는 사람들이 이해가 안가"
    "너무 흥미로워요 시즌2도 나왔으면 좋겠어요"
    "이게 무슨 영화야 지루하기짝이없네"
    "배울점이 많은 영화네요"
]

In [ ]:
def wrapper_generate(model, input_prompt, do_stream=False):
    data = tokenizer(input_prompt, return_tensors="pt")
    streamer = TextStreamer(tokenizer, skip_prompt=True, skip_special_tokens=True)
    input_ids = data.input_ids[..., :-1]
    with torch.no_grad():
        pred = model.generate(
            input_ids=input_ids.cuda(),
            streamer=streamer if do_stream else None,
            use_cache=True,
            max_new_tokens=float('inf'),
            do_sample=False
        )
    decoded_text = tokenizer.batch_decode(pred, skip_special_tokens=True)
    decoded_text = decoded_text[0].replace("<[!newline]>", "\n")
    return (decoded_text[len(input_prompt):])

In [ ]:
eval_dic = {i:wrapper_generate(model=base_model, input_prompt=prompt_template.format(System=default_system_msg, User=evaluation_queries[i]))for i, query in enumerate(evaluation_queries)}

/usr/local/lib/python3.10/dist-packages/transformers/generation/utils.py:1473: UserWarning: You have modified the pretrained model configuration to control generation. This is a deprecated strategy to control generation and will be removed soon, in a future version. Please use and modify the model generation configuration (see https://huggingface.co/docs/transformers/generation_strategies#default-text-generation-configuration )
  warnings.warn(


In [ ]:
print(eval_dic[0])

- 분석 결과 0: 음식명:치즈돈까스, 수량:한 판
- 분석 결과 1: 음식명:아메리카노, 옵션:아이스, 수량:한 잔


# 미세튜닝된 모델 로딩 후 테스트

In [ ]:
bnb_config = BitsAndBytesConfig(
    load_in_4bit=True,
    bnb_4bit_quant_type="nf4",
    bnb_4bit_compute_dtype=torch.bfloat16,
) # save_model한 모델 체크포인트가져와서 로딩

In [ ]:

trained_model = AutoPeftModelForCausalLM.from_pretrained(
    script_args.training_args.output_dir,
    quantization_config=bnb_config,
    device_map="auto",
    cache_dir=script_args.cache_dir,
    trust_remote_code=True,

)

ValueError: ignored

In [ ]:
tokenizer = AutoTokenizer.from_pretrained(
    script_args.model_name,
    trust_remote_code=True,
    cache_dir=script_args.cache_dir,
)

if getattr(tokenizer, "pad_token", None) is None:
    tokenizer.pad_token = tokenizer.eos_token
tokenizer.padding_side = "right"  # Fix weird overflow issue with fp16 training
trained_model.config.pad_token_id = tokenizer.pad_token_id

ValueError: ignored

추론 과정에서는 GPU 메모리를 약 5.5 GB 활용

In [ ]:
eval_dic = {i:wrapper_generate(model=trained_model, input_prompt=prompt_template.format(System=default_system_msg, User=evaluation_queries[i]))for i, query in enumerate(evaluation_queries)}

In [ ]:
print(eval_dic[0])